## Business Problem

## Import Packages

In [1]:
import pandas as pd
import numpy as np

pd.set_option('display.max_columns', 10000)

In [2]:
df=pd.read_csv('judge-1377884607_tweet_product_company.csv',encoding = 'unicode_escape')

## Data Cleaning

In [3]:
df.head()

tweet_text  \
0  .@wesley83 I have a 3G iPhone. After 3 hrs twe...   
1  @jessedee Know about @fludapp ? Awesome iPad/i...   
2  @swonderlin Can not wait for #iPad 2 also. The...   
3  @sxsw I hope this year's festival isn't as cra...   
4  @sxtxstate great stuff on Fri #SXSW: Marissa M...   

  emotion_in_tweet_is_directed_at  \
0                          iPhone   
1              iPad or iPhone App   
2                            iPad   
3              iPad or iPhone App   
4                          Google   

  is_there_an_emotion_directed_at_a_brand_or_product  
0                                   Negative emotion  
1                                   Positive emotion  
2                                   Positive emotion  
3                                   Negative emotion  
4                                   Positive emotion

In [4]:
df.emotion_in_tweet_is_directed_at.value_counts()

iPad                               946
Apple                              661
iPad or iPhone App                 470
Google                             430
iPhone                             297
Other Google product or service    293
Android App                         81
Android                             78
Other Apple product or service      35
Name: emotion_in_tweet_is_directed_at, dtype: int64

In [5]:
df.is_there_an_emotion_directed_at_a_brand_or_product.value_counts()

No emotion toward brand or product    5389
Positive emotion                      2978
Negative emotion                       570
I can't tell                           156
Name: is_there_an_emotion_directed_at_a_brand_or_product, dtype: int64

In [6]:
df.is_there_an_emotion_directed_at_a_brand_or_product.isna().sum()

0

In [7]:
df.emotion_in_tweet_is_directed_at.isna().sum()

5802

In [8]:
df.shape

(9093, 3)

In [9]:
df.columns=['tweet','company','emotion']

In [10]:
df=df.drop([6]).reset_index(drop=True)

In [11]:
df.emotion.value_counts()

No emotion toward brand or product    5388
Positive emotion                      2978
Negative emotion                       570
I can't tell                           156
Name: emotion, dtype: int64

In [12]:
df['emotion'] = df['emotion'].apply(lambda x: "No emotion toward brand or product" if x == "I can't tell" else x)

In [13]:
df['emotion'].value_counts()

No emotion toward brand or product    5544
Positive emotion                      2978
Negative emotion                       570
Name: emotion, dtype: int64

In [14]:
df.tweet.dropna(inplace=True)

In [15]:
df[df.company.isna()].head()

tweet company  \
5   @teachntech00 New iPad Apps For #SpeechTherapy...     NaN   
15  Holler Gram for iPad on the iTunes App Store -...     NaN   
31  Attn: All  #SXSW frineds, @mention Register fo...     NaN   
32      Anyone at  #sxsw want to sell their old iPad?     NaN   
33  Anyone at  #SXSW who bought the new iPad want ...     NaN   

                               emotion  
5   No emotion toward brand or product  
15  No emotion toward brand or product  
31  No emotion toward brand or product  
32  No emotion toward brand or product  
33  No emotion toward brand or product

In [16]:
df[df.emotion=='No emotion toward brand or product'].company.value_counts()

iPad                               28
Apple                              23
Google                             16
iPad or iPhone App                 10
iPhone                             10
Other Google product or service    10
Other Apple product or service      1
Android                             1
Android App                         1
Name: company, dtype: int64

In [17]:
df[df.emotion=='No emotion toward brand or product'].company.isna().sum()

5444

In [18]:
df.head()

tweet             company  \
0  .@wesley83 I have a 3G iPhone. After 3 hrs twe...              iPhone   
1  @jessedee Know about @fludapp ? Awesome iPad/i...  iPad or iPhone App   
2  @swonderlin Can not wait for #iPad 2 also. The...                iPad   
3  @sxsw I hope this year's festival isn't as cra...  iPad or iPhone App   
4  @sxtxstate great stuff on Fri #SXSW: Marissa M...              Google   

            emotion  
0  Negative emotion  
1  Positive emotion  
2  Positive emotion  
3  Negative emotion  
4  Positive emotion

In [19]:
# Apply a first round of text cleaning techniques
import re
import string

def clean_text_round1(text):
    '''Make text lowercase, remove text in square brackets, remove punctuation and remove words containing numbers.'''
    text = text.lower()
    text = re.sub('[%s]' % re.escape(string.punctuation), ' ', text)
    text = re.sub('\w*\d\w*', ' ', text)
    text = re.sub(r'^https?:\/\/.*[\r\n]*', ' ', text, flags=re.MULTILINE)

    return text

round1 = lambda x: clean_text_round1(x)
    

In [20]:
# Let's look how the cleaned tweets look like
df['clean_tweets'] = pd.DataFrame(df.tweet.apply(round1))
df.head()

tweet             company  \
0  .@wesley83 I have a 3G iPhone. After 3 hrs twe...              iPhone   
1  @jessedee Know about @fludapp ? Awesome iPad/i...  iPad or iPhone App   
2  @swonderlin Can not wait for #iPad 2 also. The...                iPad   
3  @sxsw I hope this year's festival isn't as cra...  iPad or iPhone App   
4  @sxtxstate great stuff on Fri #SXSW: Marissa M...              Google   

            emotion                                       clean_tweets  
0  Negative emotion      i have a   iphone  after   hrs tweeting at...  
1  Positive emotion   jessedee know about  fludapp   awesome ipad i...  
2  Positive emotion   swonderlin can not wait for  ipad   also  the...  
3  Negative emotion   sxsw i hope this year s festival isn t as cra...  
4  Positive emotion   sxtxstate great stuff on fri  sxsw  marissa m...

In [21]:
# We will clean the punctuation in case we missed something
punctuation=[",",".","#","!","@","$","?","$","%","&","-","_",":","=", "/",";",'(',")", "{","}","|"]
apple=['iPhone',"iphones",'i phones',"iPad&quot;","iphone ",'i Pad','i Pad',"Apple.","iPad?","#iPad","#iPhone",'iPad','Mac',"iphone,",'iPod','ipod','ipad','mac','Apple','apple','Apple\'s','apple\'s',"#Apple",'#apple','I-Pad']
google=['Google','google','android','Android','Google.','android,',"#android",'Google\'s','google\'s','googles' ,'#google','#Google']

In [22]:
for index in df.index:
    tweet="".join(i if i not in punctuation else " " for i in df.tweet[index])
    condition=0
    df.tweet[index]=tweet

    
    if bool(set(tweet.split())&set(apple))==True:
        df.company[index]=(list(set(tweet.split())&set(apple))[0].title().strip('\'s')).strip('\'S')
        condition=1
    else:
        condition=0
        
    if (bool(set(tweet.split())&set(google))==True) and condition==0:
        df.company[index]=(list(set(tweet.split())&set(google))[0].title().strip('\'s')).strip('\'S')
        
    elif (bool(set(tweet.split())&set(google))==True) and condition==1:
        df.company[index]+= " & "+(list(set(tweet.split())&set(google))[0].title().strip('\'s')).strip('\'S')

In [23]:
# df['company'] = df['company'].apply(lambda x: "iPad" if x == "ipad" else x)
# df['company'] = df['company'].apply(lambda x: "iPhone" if x == "iphone" else x)

In [24]:
df.company.value_counts()

Google                             2413
Apple                              1962
Ipad                               1813
Iphone                             1166
Android                             379
Iphone & Android                    137
iPad or iPhone App                   54
iPad                                 52
iPhone                               41
Mac                                  30
Ipad & Android                       24
Apple & Google                       23
Ipod                                 21
Other Apple product or service       12
Apple & Android                       7
Ipad & Google                         5
Iphone & Google                       4
Other Google product or service       2
Mac & Android                         1
Ipod & Android                        1
Name: company, dtype: int64

In [25]:
df[df['company'] == 'Apple']

tweet company  \
8     Counting down the days to  sxsw plus strong Ca...   Apple   
19    Need to buy an iPad2 while I'm in Austin at  s...   Apple   
30    You must have this app for your iPad if you ar...   Apple   
35    The best   RT  mention Ha  First in line for  ...   Apple   
39     mention    Great weather to greet you for  sx...   Apple   
...                                                 ...     ...   
9061   mention you should find  mention or   you can...   Apple   
9063   mention you should see the line here at  SXSW...   Apple   
9064  Soooo do you think Apple will have a mobile st...   Apple   
9065  How much you want to bet Apple is disproportio...   Apple   
9081   Apple guys screaming and running by line to o...   Apple   

                                 emotion  \
8                       Positive emotion   
19                      Positive emotion   
30                      Positive emotion   
35                      Positive emotion   
39                      Positive emotion   
...                                  ...   
9061  No emotion toward brand or product   
9063                    Positive emotion   
9064  No emotion toward brand or product   
9065  No emotion toward brand or product   
9081  No emotion toward brand or product   

                                           clean_tweets  
8     counting down the days to  sxsw plus strong ca...  
19    need to buy an   while i m in austin at  sxsw ...  
30    you must have this app for your ipad if you ar...  
35    the best   rt  mention ha  first in line for  ...  
39     mention    great weather to greet you for  sx...  
...                                                 ...  
9061   mention you should find  mention or   you can...  
9063   mention you should see the line here at  sxsw...  
9064  soooo do you think apple will have a mobile st...  
9065  how much you want to bet apple is disproportio...  
9081   apple guys screaming and running by line to o...  

[1962 rows x 4 columns]

In [26]:
# df[['company','emotion','tweet']].groupby(['company','emotion']).count()

## Organizing the Data

### Document-Term Matrix

In [27]:
# We are going to create a document-term matrix using CountVectorizer, and exclude common English stop words
from sklearn.feature_extraction.text import CountVectorizer

cv = CountVectorizer(stop_words='english')
data_cv = cv.fit_transform(df.clean_tweets)
df_cv = pd.DataFrame(data_cv.toarray(), columns=cv.get_feature_names())
df_cv.index = df.index
df_cv

aapl  aaron  aarpbulletin  ab  abacus  abandoned  abba  aber  abilities  \
0        0      0             0   0       0          0     0     0          0   
1        0      0             0   0       0          0     0     0          0   
2        0      0             0   0       0          0     0     0          0   
3        0      0             0   0       0          0     0     0          0   
4        0      0             0   0       0          0     0     0          0   
...    ...    ...           ...  ..     ...        ...   ...   ...        ...   
9087     0      0             0   0       0          0     0     0          0   
9088     0      0             0   0       0          0     0     0          0   
9089     0      0             0   0       0          0     0     0          0   
9090     0      0             0   0       0          0     0     0          0   
9091     0      0             0   0       0          0     0     0          0   

      ability  able  abnormal  abound  abroad  absolute  absolutely  \
0           0     0         0       0       0         0           0   
1           0     0         0       0       0         0           0   
2           0     0         0       0       0         0           0   
3           0     0         0       0       0         0           0   
4           0     0         0       0       0         0           0   
...       ...   ...       ...     ...     ...       ...         ...   
9087        0     0         0       0       0         0           0   
9088        0     0         0       0       0         0           0   
9089        0     0         0       0       0         0           0   
9090        0     0         0       0       0         0           0   
9091        0     0         0       0       0         0           0   

      absolutley  abt  abuzz  academy  acc  accelerater  acceleration  \
0              0    0      0        0    0            0             0   
1              0    0      0        0    0            0             0   
2              0    0      0        0    0            0             0   
3              0    0      0        0    0            0             0   
4              0    0      0        0    0            0             0   
...          ...  ...    ...      ...  ...          ...           ...   
9087           0    0      0        0    0            0             0   
9088           0    0      0        0    0            0             0   
9089           0    0      0        0    0            0             0   
9090           0    0      0        0    0            0             0   
9091           0    0      0        0    0            0             0   

      accelerator  accept  acceptable  access  accessibility  accessible  \
0               0       0           0       0              0           0   
1               0       0           0       0              0           0   
2               0       0           0       0              0           0   
3               0       0           0       0              0           0   
4               0       0           0       0              0           0   
...           ...     ...         ...     ...            ...         ...   
9087            0       0           0       0              0           0   
9088            0       0           0       0              0           0   
9089            0       0           0       0              0           0   
9090            0       0           0       0              0           0   
9091            0       0           0       0              0           0   

      accessories  accessory  accesssxsw  accidentally  accommodate  \
0               0          0           0             0            0   
1               0          0           0             0            0   
2               0          0           0             0            0   
3               0          0           0             0            0   
4               0          0       

## EDA

In [28]:
df_cv.head()

aapl  aaron  aarpbulletin  ab  abacus  abandoned  abba  aber  abilities  \
0     0      0             0   0       0          0     0     0          0   
1     0      0             0   0       0          0     0     0          0   
2     0      0             0   0       0          0     0     0          0   
3     0      0             0   0       0          0     0     0          0   
4     0      0             0   0       0          0     0     0          0   

   ability  able  abnormal  abound  abroad  absolute  absolutely  absolutley  \
0        0     0         0       0       0         0           0           0   
1        0     0         0       0       0         0           0           0   
2        0     0         0       0       0         0           0           0   
3        0     0         0       0       0         0           0           0   
4        0     0         0       0       0         0           0           0   

   abt  abuzz  academy  acc  accelerater  acceleration  accelerator  accept  \
0    0      0        0    0            0             0            0       0   
1    0      0        0    0            0             0            0       0   
2    0      0        0    0            0             0            0       0   
3    0      0        0    0            0             0            0       0   
4    0      0        0    0            0             0            0       0   

   acceptable  access  accessibility  accessible  accessories  accessory  \
0           0       0              0           0            0          0   
1           0       0              0           0            0          0   
2           0       0              0           0            0          0   
3           0       0              0           0            0          0   
4           0       0              0           0            0          0   

   accesssxsw  accidentally  accommodate  accompanied  accomplish  according  \
0           0             0            0            0           0          0   
1           0             0            0            0           0          0   
2           0             0            0            0           0          0   
3           0             0            0            0           0          0   
4           0             0            0            0           0          0   

   accordion  account  accounts  accuracy  acerbic  achieve  achievement  \
0          0        0         0         0        0        0            0   
1          0        0         0         0        0        0            0   
2          0        0         0         0        0        0            0   
3          0        0         0         0        0        0            0   
4          0        0         0         0        0        0            0   

   acknowledge  ackward  aclu  aclus  acoustic  acquired  acquisition  \
0            0        0     0      0         0         0            0   
1            0        0     0      0         0         0            0   
2            0        0     0      0         0         0            0   
3            0        0     0      0         0         0            0   
4            0        0     0      0         0         0            0   

   acrosse  act  acting  action  actionable  actions  activate  activations  \
0        0    0       0       0           0        0         0            0   
1        0    0       0       0           0        0         0            0   
2        0    0       0       0           0        0         0            0   
3        0    0       0       0           0        0         0            0   
4        0    0       0       0           0        0         0            0   

   activity  actors  acts  actsofsharing  actual  actually  ad  adam  adams  \
0         0       0     0              0       0         0   0     0      0   
1         0       0     0              0       0         0   0     0      0   
2         0       0     0       

In [29]:
df.clean_tweet

AttributeError: 'DataFrame' object has no attribute 'clean_tweet'

In [ ]:
# Breaks the code on purpose, so we don't run two vectorizer
df.h ead()

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk.corpus import stopwords 
from nltk.tokenize import RegexpTokenizer

stopwords = ['am','he','i','the','hi']

vectorizer = TfidfVectorizer(ngram_range=(1,1),stop_words=stopwords, token_pattern=(r'[a-zA-Z]+'))

text_tf = vectorizer.fit_transform(df['tweet'])
text_tf.data

In [ ]:
text_tf

In [ ]:
pd.DataFrame(text_tf)

In [ ]:
df = pd.DataFrame(text_tf.todense(),columns = vectorizer.get_feature_names())
df